# Data Exploration and Preprocessing

This notebook explores the book recommendation datasets and performs initial preprocessing steps.

## Datasets:
- **Books.csv**: Book information (ISBN, Title, Author, Year, Publisher, Images)
- **Users.csv**: User information (User-ID, Location, Age)
- **Ratings.csv**: User-book ratings (User-ID, ISBN, Rating 0-10)

In [51]:
# Import required libraries
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import warnings
warnings.filterwarnings('ignore')
# Import additional libraries for DLRM data preparation
import os
from shutil import rmtree
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.model_selection import train_test_split
from streaming import MDSWriter
from tqdm import tqdm
import pickle
# Set up plotting
plt.style.use('seaborn-v0_8')
sns.set_palette("husl")


from recommendation_system.src.data.preprocessing import DataPreprocessor, load_and_preprocess_data

## 1. Load and Examine Raw Data

In [52]:
# Initialize preprocessor
preprocessor = DataPreprocessor(data_path='../')

# Load data
books_df, users_df, ratings_df = preprocessor.load_data()

print("Dataset shapes:")
print(f"Books: {books_df.shape}")
print(f"Users: {users_df.shape}")
print(f"Ratings: {ratings_df.shape}")

INFO:recommendation_system.src.data.preprocessing:Loading datasets...
INFO:recommendation_system.src.data.preprocessing:Loaded books data: (271360, 8)
INFO:recommendation_system.src.data.preprocessing:Loaded users data: (278858, 3)
INFO:recommendation_system.src.data.preprocessing:Loaded ratings data: (1149780, 3)


Dataset shapes:
Books: (271360, 8)
Users: (278858, 3)
Ratings: (1149780, 3)


In [53]:
# Get detailed data information
data_info = preprocessor.get_data_info()

for dataset_name, info in data_info.items():
    print(f"\n=== {dataset_name.upper()} DATASET ===")
    print(f"Shape: {info['shape']}")
    print(f"Columns: {info['columns']}")
    print(f"Data types: {info['dtypes']}")
    print(f"Missing values: {info['missing_values']}")


=== BOOKS DATASET ===
Shape: (271360, 8)
Columns: ['ISBN', 'Book-Title', 'Book-Author', 'Year-Of-Publication', 'Publisher', 'Image-URL-S', 'Image-URL-M', 'Image-URL-L']
Data types: {'ISBN': dtype('O'), 'Book-Title': dtype('O'), 'Book-Author': dtype('O'), 'Year-Of-Publication': dtype('O'), 'Publisher': dtype('O'), 'Image-URL-S': dtype('O'), 'Image-URL-M': dtype('O'), 'Image-URL-L': dtype('O')}
Missing values: {'ISBN': 0, 'Book-Title': 0, 'Book-Author': 2, 'Year-Of-Publication': 0, 'Publisher': 2, 'Image-URL-S': 0, 'Image-URL-M': 0, 'Image-URL-L': 3}

=== USERS DATASET ===
Shape: (278858, 3)
Columns: ['User-ID', 'Location', 'Age']
Data types: {'User-ID': dtype('int64'), 'Location': dtype('O'), 'Age': dtype('float64')}
Missing values: {'User-ID': 0, 'Location': 0, 'Age': 110762}

=== RATINGS DATASET ===
Shape: (1149780, 3)
Columns: ['User-ID', 'ISBN', 'Book-Rating']
Data types: {'User-ID': dtype('int64'), 'ISBN': dtype('O'), 'Book-Rating': dtype('int64')}
Missing values: {'User-ID': 0, '

## 2. Books Dataset Analysis

In [54]:
# Display first few rows
print("First 5 rows of Books dataset:")
display(books_df.head())

print("\nBooks dataset info:")
books_df.info()

First 5 rows of Books dataset:


ISBN                                         Book-Title  \
0  0195153448                                Classical Mythology   
1  0002005018                                       Clara Callan   
2  0060973129                               Decision in Normandy   
3  0374157065  Flu: The Story of the Great Influenza Pandemic...   
4  0393045218                             The Mummies of Urumchi   

            Book-Author Year-Of-Publication                   Publisher  \
0    Mark P. O. Morford                2002     Oxford University Press   
1  Richard Bruce Wright                2001       HarperFlamingo Canada   
2          Carlo D'Este                1991             HarperPerennial   
3      Gina Bari Kolata                1999        Farrar Straus Giroux   
4       E. J. W. Barber                1999  W. W. Norton &amp; Company   

                                         Image-URL-S  \
0  http://images.amazon.com/images/P/0195153448.0...   
1  http://images.amazon.com/images/P/0002005018.0...   
2  http://images.amazon.com/images/P/0060973129.0...   
3  http://images.amazon.com/images/P/0374157065.0...   
4  http://images.amazon.com/images/P/0393045218.0...   

                                         Image-URL-M  \
0  http://images.amazon.com/images/P/0195153448.0...   
1  http://images.amazon.com/images/P/0002005018.0...   
2  http://images.amazon.com/images/P/0060973129.0...   
3  http://images.amazon.com/images/P/0374157065.0...   
4  http://images.amazon.com/images/P/0393045218.0...   

                                         Image-URL-L  
0  http://images.amazon.com/images/P/0195153448.0...  
1  http://images.amazon.com/images/P/0002005018.0...  
2  http://images.amazon.com/images/P/0060973129.0...  
3  http://images.amazon.com/images/P/0374157065.0...  
4  http://images.amazon.com/images/P/0393045218.0...


Books dataset info:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 271360 entries, 0 to 271359
Data columns (total 8 columns):
 #   Column               Non-Null Count   Dtype 
---  ------               --------------   ----- 
 0   ISBN                 271360 non-null  object
 1   Book-Title           271360 non-null  object
 2   Book-Author          271358 non-null  object
 3   Year-Of-Publication  271360 non-null  object
 4   Publisher            271358 non-null  object
 5   Image-URL-S          271360 non-null  object
 6   Image-URL-M          271360 non-null  object
 7   Image-URL-L          271357 non-null  object
dtypes: object(8)
memory usage: 16.6+ MB


In [55]:
# Analyze publication years
books_df['Year-Of-Publication'] = pd.to_numeric(books_df['Year-Of-Publication'], errors='coerce')

# Publication year distribution
fig = make_subplots(rows=2, cols=2, 
                    subplot_titles=['Publication Year Distribution', 'Missing Values Analysis',
                                   'Top Publishers', 'Books per Author'],
                    specs=[[{"type": "scatter"}, {"type": "bar"}],
                           [{"type": "bar", "colspan": 2}, None]])

# Publication year histogram
valid_years = books_df['Year-Of-Publication'].dropna()
valid_years = valid_years[(valid_years >= 1900) & (valid_years <= 2024)]
fig.add_trace(go.Histogram(x=valid_years, name="Publication Years", nbinsx=50), row=1, col=1)

# Missing values
missing_data = books_df.isnull().sum()
fig.add_trace(go.Bar(x=missing_data.index, y=missing_data.values, name="Missing Values"), row=1, col=2)

# Top publishers
top_publishers = books_df['Publisher'].value_counts().head(15)
fig.add_trace(go.Bar(x=top_publishers.index, y=top_publishers.values, name="Top Publishers"), row=2, col=1)

fig.update_layout(height=800, showlegend=False, title_text="Books Dataset Analysis")
fig.show()

## 3. Users Dataset Analysis

In [56]:
# Display first few rows
print("First 5 rows of Users dataset:")
display(users_df.head())

print("\nUsers dataset info:")
users_df.info()

First 5 rows of Users dataset:


User-ID                            Location   Age
0        1                  nyc, new york, usa   NaN
1        2           stockton, california, usa  18.0
2        3     moscow, yukon territory, russia   NaN
3        4           porto, v.n.gaia, portugal  17.0
4        5  farnborough, hants, united kingdom   NaN


Users dataset info:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 278858 entries, 0 to 278857
Data columns (total 3 columns):
 #   Column    Non-Null Count   Dtype  
---  ------    --------------   -----  
 0   User-ID   278858 non-null  int64  
 1   Location  278858 non-null  object 
 2   Age       168096 non-null  float64
dtypes: float64(1), int64(1), object(1)
memory usage: 6.4+ MB


In [57]:
# Age analysis
users_df['Age'] = pd.to_numeric(users_df['Age'], errors='coerce')

fig = make_subplots(rows=2, cols=2,
                    subplot_titles=['Age Distribution', 'Missing Age Values',
                                   'Top Locations', 'Age Statistics'],
                    specs=[[{"type": "scatter"}, {"type": "bar"}],
                           [{"type": "bar"}, {"type": "table"}]])

# Age distribution
valid_ages = users_df['Age'].dropna()
valid_ages = valid_ages[(valid_ages >= 5) & (valid_ages <= 100)]
fig.add_trace(go.Histogram(x=valid_ages, name="Age Distribution", nbinsx=30), row=1, col=1)

# Missing values by column
missing_users = users_df.isnull().sum()
fig.add_trace(go.Bar(x=missing_users.index, y=missing_users.values, name="Missing Values"), row=1, col=2)

# Top locations
top_locations = users_df['Location'].value_counts().head(15)
fig.add_trace(go.Bar(x=top_locations.index, y=top_locations.values, name="Top Locations"), row=2, col=1)

# Age statistics table
age_stats = valid_ages.describe()
fig.add_trace(go.Table(
    header=dict(values=['Statistic', 'Value']),
    cells=dict(values=[age_stats.index, age_stats.values.round(2)])
), row=2, col=2)

fig.update_layout(height=800, showlegend=False, title_text="Users Dataset Analysis")
fig.show()

## 4. Ratings Dataset Analysis

In [58]:
# Display first few rows
print("First 5 rows of Ratings dataset:")
display(ratings_df.head())

print("\nRatings dataset info:")
ratings_df.info()

First 5 rows of Ratings dataset:


User-ID        ISBN  Book-Rating
0   276725  034545104X            0
1   276726  0155061224            5
2   276727  0446520802            0
3   276729  052165615X            3
4   276729  0521795028            6


Ratings dataset info:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1149780 entries, 0 to 1149779
Data columns (total 3 columns):
 #   Column       Non-Null Count    Dtype 
---  ------       --------------    ----- 
 0   User-ID      1149780 non-null  int64 
 1   ISBN         1149780 non-null  object
 2   Book-Rating  1149780 non-null  int64 
dtypes: int64(2), object(1)
memory usage: 26.3+ MB


In [59]:
# Rating distribution analysis
fig = make_subplots(rows=2, cols=2,
                    subplot_titles=['Rating Distribution', 'Ratings per User',
                                   'Ratings per Book', 'Rating Matrix Sparsity'],
                    specs=[[{"type": "bar"}, {"type": "xy"}],
                           [{"type": "xy"}, {"type": "table"}]])

# Rating distribution
rating_counts = ratings_df['Book-Rating'].value_counts().sort_index()
fig.add_trace(go.Bar(x=rating_counts.index, y=rating_counts.values, name="Rating Distribution"), row=1, col=1)

# Ratings per user distribution
user_rating_counts = ratings_df.groupby('User-ID').size()
fig.add_trace(go.Histogram(x=user_rating_counts, name="Ratings per User", nbinsx=50), row=1, col=2)

# Ratings per book distribution
book_rating_counts = ratings_df.groupby('ISBN').size()
fig.add_trace(go.Histogram(x=book_rating_counts, name="Ratings per Book", nbinsx=50), row=2, col=1)

# Sparsity analysis
n_users = ratings_df['User-ID'].nunique()
n_books = ratings_df['ISBN'].nunique()
n_ratings = len(ratings_df)
sparsity = 1 - (n_ratings / (n_users * n_books))

sparsity_data = [
    ['Total Users', n_users],
    ['Total Books', n_books],
    ['Total Ratings', n_ratings],
    ['Possible Interactions', n_users * n_books],
    ['Sparsity', f"{sparsity:.4%}"]
]

fig.add_trace(go.Table(
    header=dict(values=['Metric', 'Value'],
                fill_color='lightblue',
                align='left'),
    cells=dict(values=[[row[0] for row in sparsity_data], [row[1] for row in sparsity_data]],
               fill_color='white',
               align='left')
), row=2, col=2)

fig.update_layout(height=800, showlegend=False, title_text="Ratings Dataset Analysis")
fig.show()

print(f"Dataset Sparsity: {sparsity:.4%}")
print(f"Average ratings per user: {user_rating_counts.mean():.2f}")
print(f"Average ratings per book: {book_rating_counts.mean():.2f}")

Dataset Sparsity: 99.9968%
Average ratings per user: 10.92
Average ratings per book: 3.38


## 5. Data Quality Issues and Cleaning Strategy

In [60]:
# Identify data quality issues
print("=== DATA QUALITY ANALYSIS ===")

# Books issues
print("\n1. BOOKS DATASET ISSUES:")
print(f"- Missing ISBN: {books_df['ISBN'].isnull().sum()}")
print(f"- Missing titles: {books_df['Book-Title'].isnull().sum()}")
print(f"- Missing authors: {books_df['Book-Author'].isnull().sum()}")
print(f"- Invalid publication years: {books_df['Year-Of-Publication'].isnull().sum()}")

# Users issues
print("\n2. USERS DATASET ISSUES:")
print(f"- Missing User-ID: {users_df['User-ID'].isnull().sum()}")
print(f"- Missing Age: {users_df['Age'].isnull().sum()}")
print(f"- Missing Location: {users_df['Location'].isnull().sum()}")

# Ratings issues
print("\n3. RATINGS DATASET ISSUES:")
print(f"- Missing User-ID: {ratings_df['User-ID'].isnull().sum()}")
print(f"- Missing ISBN: {ratings_df['ISBN'].isnull().sum()}")
print(f"- Missing Rating: {ratings_df['Book-Rating'].isnull().sum()}")
print(f"- Invalid ratings (outside 0-10): {((ratings_df['Book-Rating'] < 0) | (ratings_df['Book-Rating'] > 10)).sum()}")

# Cross-dataset consistency
users_in_ratings = set(ratings_df['User-ID'].unique())
users_in_users_df = set(users_df['User-ID'].unique())
books_in_ratings = set(ratings_df['ISBN'].unique())
books_in_books_df = set(books_df['ISBN'].unique())

print("\n4. CROSS-DATASET CONSISTENCY:")
print(f"- Users in ratings but not in users.csv: {len(users_in_ratings - users_in_users_df)}")
print(f"- Books in ratings but not in books.csv: {len(books_in_ratings - books_in_books_df)}")
print(f"- Users in users.csv but not in ratings: {len(users_in_users_df - users_in_ratings)}")
print(f"- Books in books.csv but not in ratings: {len(books_in_books_df - books_in_ratings)}")

=== DATA QUALITY ANALYSIS ===

1. BOOKS DATASET ISSUES:
- Missing ISBN: 0
- Missing titles: 0
- Missing authors: 2
- Invalid publication years: 3

2. USERS DATASET ISSUES:
- Missing User-ID: 0
- Missing Age: 110762
- Missing Location: 0

3. RATINGS DATASET ISSUES:
- Missing User-ID: 0
- Missing ISBN: 0
- Missing Rating: 0
- Invalid ratings (outside 0-10): 0

4. CROSS-DATASET CONSISTENCY:
- Users in ratings but not in users.csv: 0
- Books in ratings but not in books.csv: 70405
- Users in users.csv but not in ratings: 173575
- Books in books.csv but not in ratings: 1209


## 6. Apply Data Cleaning and Filtering

In [61]:
# Apply cleaning and filtering to reduce sparsity
print("Applying data cleaning and filtering...")

# Test different filtering thresholds
filtering_results = []

for min_user_ratings in [5, 10, 20]:
    for min_book_ratings in [5, 10, 20]:
        try:
            books_filtered, users_filtered, ratings_filtered = preprocessor.filter_sparse_data(
                min_user_ratings=min_user_ratings,
                min_book_ratings=min_book_ratings
            )
            
            n_users_f = len(users_filtered)
            n_books_f = len(books_filtered)
            n_ratings_f = len(ratings_filtered)
            sparsity_f = 1 - (n_ratings_f / (n_users_f * n_books_f))
            
            filtering_results.append({
                'min_user_ratings': min_user_ratings,
                'min_book_ratings': min_book_ratings,
                'n_users': n_users_f,
                'n_books': n_books_f,
                'n_ratings': n_ratings_f,
                'sparsity': sparsity_f,
                'coverage': n_ratings_f / len(ratings_df)
            })
        except Exception as e:
            print(f"Error with min_user_ratings={min_user_ratings}, min_book_ratings={min_book_ratings}: {e}")

# Display filtering results
filtering_df = pd.DataFrame(filtering_results)
print("\nFiltering Results:")
display(filtering_df)

INFO:recommendation_system.src.data.preprocessing:Filtering sparse data...
INFO:recommendation_system.src.data.preprocessing:Cleaning books data...


Applying data cleaning and filtering...


INFO:recommendation_system.src.data.preprocessing:Books data cleaned: (266723, 8)
INFO:recommendation_system.src.data.preprocessing:Cleaning users data...
INFO:recommendation_system.src.data.preprocessing:Users data cleaned: (277610, 3)
INFO:recommendation_system.src.data.preprocessing:Cleaning ratings data...
INFO:recommendation_system.src.data.preprocessing:Ratings data cleaned: (1149780, 3)
INFO:recommendation_system.src.data.preprocessing:Filtering iteration 1
INFO:recommendation_system.src.data.preprocessing:Filtering iteration 2
INFO:recommendation_system.src.data.preprocessing:Filtering iteration 3
INFO:recommendation_system.src.data.preprocessing:Filtering iteration 4
INFO:recommendation_system.src.data.preprocessing:Filtering iteration 5
INFO:recommendation_system.src.data.preprocessing:Filtering iteration 6
INFO:recommendation_system.src.data.preprocessing:Filtering iteration 7
INFO:recommendation_system.src.data.preprocessing:Filtering iteration 8
INFO:recommendation_system.


Filtering Results:


min_user_ratings  min_book_ratings  n_users  n_books  n_ratings  sparsity  \
0                 5                 5    15716    35714     585579  0.998957   
1                 5                10    12985    14610     429205  0.997738   
2                 5                20    10295     5804     296471  0.995038   
3                10                 5     8481    33115     526097  0.998127   
4                10                10     6731    13176     374486  0.995777   
5                10                20     5203     5088     248993  0.990594   
6                20                 5     4509    29995     458430  0.996610   
7                20                10     3564    11655     317250  0.992362   
8                20                20     2568     4271     197140  0.982026   

   coverage  
0  0.509297  
1  0.373293  
2  0.257850  
3  0.457563  
4  0.325702  
5  0.216557  
6  0.398711  
7  0.275922  
8  0.171459

## 7. Final Preprocessed Dataset

In [62]:
# Apply the best configuration for further analysis
best_idx = filtering_df['sparsity'].idxmin()
best_config = filtering_df.iloc[best_idx]
best_min_user = int(best_config['min_user_ratings'])
best_min_book = int(best_config['min_book_ratings'])

books_final, users_final, ratings_final = preprocessor.filter_sparse_data(
    min_user_ratings=best_min_user,
    min_book_ratings=best_min_book
)

print("=== FINAL PREPROCESSED DATASET ===")
print(f"Books: {len(books_final)}")
print(f"Users: {len(users_final)}")
print(f"Ratings: {len(ratings_final)}")
print(f"Sparsity: {1 - (len(ratings_final) / (len(users_final) * len(books_final))):.4%}")
print(f"Coverage: {len(ratings_final) / len(ratings_df):.4%} of original ratings retained")

INFO:recommendation_system.src.data.preprocessing:Filtering sparse data...
INFO:recommendation_system.src.data.preprocessing:Cleaning books data...
INFO:recommendation_system.src.data.preprocessing:Books data cleaned: (266723, 8)
INFO:recommendation_system.src.data.preprocessing:Cleaning users data...
INFO:recommendation_system.src.data.preprocessing:Users data cleaned: (277610, 3)
INFO:recommendation_system.src.data.preprocessing:Cleaning ratings data...
INFO:recommendation_system.src.data.preprocessing:Ratings data cleaned: (1149780, 3)
INFO:recommendation_system.src.data.preprocessing:Filtering iteration 1
INFO:recommendation_system.src.data.preprocessing:Filtering iteration 2
INFO:recommendation_system.src.data.preprocessing:Filtering iteration 3
INFO:recommendation_system.src.data.preprocessing:Filtering iteration 4
INFO:recommendation_system.src.data.preprocessing:Filtering iteration 5
INFO:recommendation_system.src.data.preprocessing:Filtering iteration 6
INFO:recommendation_sys

=== FINAL PREPROCESSED DATASET ===
Books: 4271
Users: 2568
Ratings: 197140
Sparsity: 98.2026%
Coverage: 17.1459% of original ratings retained


In [63]:
import os

# Create data directory in parent folder if it doesn't exist
os.makedirs('../data', exist_ok=True)

# Save preprocessed data for model training
print("Saving preprocessed data...")
books_final.to_csv('../data/books_processed.csv', index=False)
users_final.to_csv('../data/users_processed.csv', index=False)
ratings_final.to_csv('../data/ratings_processed.csv', index=False)
print("Preprocessed data saved to ../data/")

Saving preprocessed data...
Preprocessed data saved to ../data/


## 8. DLRM Feature Engineering and Data Preparation

Now we'll create DLRM-compatible features and prepare the data in MDS format for training.

In [64]:
class BookDataPreprocessor:
    """Complete preprocessor for book recommendation data with DLRM support"""
    
    def __init__(self):
        # Encoders for categorical features
        self.user_encoder = LabelEncoder()
        self.book_encoder = LabelEncoder()
        self.publisher_encoder = LabelEncoder()
        self.location_encoder = LabelEncoder()
        self.scaler = StandardScaler()
        
        # Will be set during feature creation
        self.cat_cols = []
        self.dense_cols = []
        self.emb_counts = []
    
    def load_and_preprocess_data(self, min_user_ratings=10, min_book_ratings=5, rating_threshold=6.0):
        """Load and preprocess all data for DLRM training"""
        
        print("Loading data...")
        os.makedirs('../data', exist_ok=True)
        # Load data
        books_df = pd.read_csv('../data/books_processed.csv', encoding='latin-1', low_memory=False)
        users_df = pd.read_csv('../data/users_processed.csv', encoding='latin-1', low_memory=False) 
        ratings_df = pd.read_csv('../data/ratings_processed.csv', encoding='latin-1', low_memory=False)
        

        
        # Filter for active users and popular books
        user_counts = ratings_df['User-ID'].value_counts()
        book_counts = ratings_df['ISBN'].value_counts()
        
        active_users = user_counts[user_counts >= min_user_ratings].index
        popular_books = book_counts[book_counts >= min_book_ratings].index
        
        ratings_filtered = ratings_df[
            (ratings_df['User-ID'].isin(active_users)) & 
            (ratings_df['ISBN'].isin(popular_books))
        ]
        
        print(f"After filtering:")
        print(f"  Ratings: {ratings_filtered.shape}")
        print(f"  Users retained: {ratings_filtered['User-ID'].nunique()}")
        print(f"  Books retained: {ratings_filtered['ISBN'].nunique()}")
        
        # Merge all data
        merged_df = ratings_filtered.merge(books_df, on='ISBN', how='left')
        merged_df = merged_df.merge(users_df, on='User-ID', how='left')
        
        print(f"Merged dataset shape: {merged_df.shape}")
        
        # Create features
        features_df = self._create_features(merged_df, rating_threshold)
        
        return features_df
    
    def _create_features(self, df: pd.DataFrame, rating_threshold: float) -> pd.DataFrame:
        """Create DLRM-compatible features"""
        
        processed_df = df.copy()
        
        # === CATEGORICAL FEATURES ===
        
        # 1. User ID (encoded)
        processed_df['user_id_encoded'] = self.user_encoder.fit_transform(processed_df['User-ID'].astype(str))
        
        # 2. Book ID (encoded) 
        processed_df['book_id_encoded'] = self.book_encoder.fit_transform(processed_df['ISBN'].astype(str))
        
        # 3. Publisher (encoded)
        processed_df['Publisher'] = processed_df['Publisher'].fillna('Unknown')
        processed_df['publisher_encoded'] = self.publisher_encoder.fit_transform(processed_df['Publisher'].astype(str))
        
        # 4. Location (extract country and encode)
        def extract_country(location):
            if pd.isna(location):
                return 'Unknown'
            parts = str(location).split(',')
            return parts[-1].strip().lower() if len(parts) > 0 else 'Unknown'
        
        processed_df['country'] = processed_df['Location'].apply(extract_country)
        processed_df['country_encoded'] = self.location_encoder.fit_transform(processed_df['country'])
        
        # 5. Age group
        processed_df['Age'] = pd.to_numeric(processed_df['Age'], errors='coerce')
        age_bins = [0, 18, 25, 35, 50, 65, 100]
        age_labels = [0, 1, 2, 3, 4, 5]
        processed_df['age_group'] = pd.cut(processed_df['Age'], bins=age_bins, labels=age_labels, include_lowest=True)
        processed_df['age_group'] = processed_df['age_group'].fillna(0).astype(int)
        
        # 6. Publication decade
        processed_df['Year-Of-Publication'] = pd.to_numeric(processed_df['Year-Of-Publication'], errors='coerce')
        processed_df['publication_decade'] = ((processed_df['Year-Of-Publication'] // 10) * 10).fillna(2000).astype(int)
        decade_encoder = LabelEncoder()
        processed_df['decade_encoded'] = decade_encoder.fit_transform(processed_df['publication_decade'].astype(str))
        
        # 7. Rating level (for additional categorical signal)
        rating_bins = [0, 3, 6, 8, 10]
        rating_labels = [0, 1, 2, 3]
        processed_df['rating_level'] = pd.cut(processed_df['Book-Rating'], bins=rating_bins, labels=rating_labels, include_lowest=True)
        processed_df['rating_level'] = processed_df['rating_level'].fillna(1).astype(int)
        
        # === DENSE FEATURES ===
        
        # 1. User age (normalized)
        processed_df['age_normalized'] = processed_df['Age'].fillna(processed_df['Age'].median())
        
        # 2. Publication year (normalized)
        processed_df['year_normalized'] = processed_df['Year-Of-Publication'].fillna(processed_df['Year-Of-Publication'].median())
        
        # 3. User activity (number of ratings per user)
        user_activity = processed_df.groupby('User-ID').size()
        processed_df['user_activity'] = processed_df['User-ID'].map(user_activity)
        
        # 4. Book popularity (number of ratings per book)
        book_popularity = processed_df.groupby('ISBN').size()
        processed_df['book_popularity'] = processed_df['ISBN'].map(book_popularity)
        
        # 5. User average rating
        user_avg_rating = processed_df.groupby('User-ID')['Book-Rating'].mean()
        processed_df['user_avg_rating'] = processed_df['User-ID'].map(user_avg_rating)
        
        # 6. Book average rating
        book_avg_rating = processed_df.groupby('ISBN')['Book-Rating'].mean()
        processed_df['book_avg_rating'] = processed_df['ISBN'].map(book_avg_rating)
        
        # === TARGET LABEL ===
        # Binary classification: rating >= threshold = 1, else = 0
        processed_df['label'] = (processed_df['Book-Rating'] >= rating_threshold).astype(int)
        
        # Define feature columns
        self.cat_cols = [
            'user_id_encoded', 'book_id_encoded', 'publisher_encoded', 
            'country_encoded', 'age_group', 'decade_encoded', 'rating_level'
        ]
        
        self.dense_cols = [
            'age_normalized', 'year_normalized', 'user_activity', 
            'book_popularity', 'user_avg_rating', 'book_avg_rating'
        ]
        
        # Normalize dense features
        processed_df[self.dense_cols] = self.scaler.fit_transform(processed_df[self.dense_cols])
        
        # Get embedding counts for categorical features
        self.emb_counts = [processed_df[col].nunique() for col in self.cat_cols]
        
        # Select final columns
        final_cols = ['label'] + self.dense_cols + self.cat_cols
        result_df = processed_df[final_cols].copy()
        
        print(f"Features created:")
        print(f"  Dense columns ({len(self.dense_cols)}): {self.dense_cols}")
        print(f"  Categorical columns ({len(self.cat_cols)}): {self.cat_cols}")
        print(f"  Embedding counts: {dict(zip(self.cat_cols, self.emb_counts))}")
        print(f"  Final dataset shape: {result_df.shape}")
        print(f"  Label distribution: {result_df['label'].value_counts(normalize=True).to_dict()}")
        
        return result_df
    
    def save_to_mds_format(self, df: pd.DataFrame, output_base_dir: str = "dlrm_book_data"):
        """Save preprocessed data to MDS format for DLRM training"""
        
        print("Splitting data...")
        
        # Split data: 70% train, 20% val, 10% test
        train_val_df, test_df = train_test_split(
            df, test_size=0.1, random_state=42, stratify=df['label']
        )
        
        train_df, val_df = train_test_split(
            train_val_df, test_size=0.222, random_state=42, stratify=train_val_df['label']  # 20/(70+20) = 0.222
        )
        
        print(f"Train: {len(train_df)} ({len(train_df)/len(df)*100:.1f}%)")
        print(f"Validation: {len(val_df)} ({len(val_df)/len(df)*100:.1f}%)")
        print(f"Test: {len(test_df)} ({len(test_df)/len(df)*100:.1f}%)")
        
        # Define MDS schema
        dense_dict = {key: 'float64' for key in self.dense_cols}
        cat_dict = {key: 'int64' for key in self.cat_cols}
        label_dict = {'label': 'int64'}
        columns = {**label_dict, **dense_dict, **cat_dict}
        
        # Save each split
        for data, split_name in [(train_df, 'train'), (val_df, 'validation'), (test_df, 'test')]:
            output_dir = f"{output_base_dir}/mds_{split_name}"
            self._save_split_to_mds(data, output_dir, split_name, columns)
        
        return len(train_df), len(val_df), len(test_df)
    
    def _save_split_to_mds(self, df: pd.DataFrame, output_dir: str, split_name: str, columns: dict):
        """Save a data split to MDS format"""
        
        print(f"Saving {split_name} data to {output_dir}...")
        
        # Remove existing directory
        if os.path.exists(output_dir):
            rmtree(output_dir)
        
        os.makedirs(output_dir, exist_ok=True)
        
        # Write to MDS format
        with MDSWriter(
            out=output_dir,
            columns=columns,
            compression='zstd:7'
        ) as writer:
            
            for _, row in tqdm(df.iterrows(), total=len(df), desc=f"Writing {split_name}"):
                sample = {}
                
                # Add label
                sample['label'] = int(row['label'])
                
                # Add dense features
                for col in self.dense_cols:
                    sample[col] = float(row[col])
                
                # Add categorical features
                for col in self.cat_cols:
                    sample[col] = int(row[col])
                
                writer.write(sample)
        
        print(f"✅ Saved {len(df)} {split_name} samples")





## 9. Execute DLRM Data Preparation

Now let's run the complete DLRM data preparation pipeline:

In [65]:
def prepare_book_data_for_dlrm():
    """Main function to prepare book data for DLRM training"""
    
    print("🚀 Preparing Book Data for DLRM Training")
    print("=" * 50)
    
    # Initialize preprocessor
    preprocessor = BookDataPreprocessor()
    
    # Load and preprocess data
    processed_df = preprocessor.load_and_preprocess_data(
        min_user_ratings=10,
        min_book_ratings=5,
        rating_threshold=6.0  # Ratings >= 6 are positive
    )
    
    # Save to MDS format
    train_count, val_count, test_count = preprocessor.save_to_mds_format(processed_df)
    
    # Save preprocessing info
    preprocessing_info = {
        'dense_cols': preprocessor.dense_cols,
        'cat_cols': preprocessor.cat_cols,
        'emb_counts': preprocessor.emb_counts,
        'total_samples': len(processed_df),
        'train_samples': train_count,
        'val_samples': val_count,
        'test_samples': test_count,
        'positive_rate': processed_df['label'].mean(),
        'user_encoder': preprocessor.user_encoder,
        'book_encoder': preprocessor.book_encoder,
        'publisher_encoder': preprocessor.publisher_encoder,
        'location_encoder': preprocessor.location_encoder,
        'scaler': preprocessor.scaler
    }
    
    # Save preprocessing info
    with open('../book_dlrm_preprocessing.pkl', 'wb') as f:
        pickle.dump(preprocessing_info, f)
    
    print(f"\n✅ Data preparation completed!")
    print(f"📊 Dataset ready for DLRM training:")
    print(f"   - Total samples: {len(processed_df):,}")
    print(f"   - Train: {train_count:,}")
    print(f"   - Validation: {val_count:,}")
    print(f"   - Test: {test_count:,}")
    print(f"   - Positive rate: {processed_df['label'].mean():.3f}")
    print(f"   - Dense features: {len(preprocessor.dense_cols)}")
    print(f"   - Categorical features: {len(preprocessor.cat_cols)}")
    
    return preprocessing_info

## 11. Execute the Pipeline

In [66]:
# Run the complete DLRM data preparation
preprocessing_info = prepare_book_data_for_dlrm()

🚀 Preparing Book Data for DLRM Training
Loading data...
After filtering:
  Ratings: (197140, 3)
  Users retained: 2578
  Books retained: 4313
Merged dataset shape: (197140, 12)
Features created:
  Dense columns (6): ['age_normalized', 'year_normalized', 'user_activity', 'book_popularity', 'user_avg_rating', 'book_avg_rating']
  Categorical columns (7): ['user_id_encoded', 'book_id_encoded', 'publisher_encoded', 'country_encoded', 'age_group', 'decade_encoded', 'rating_level']
  Embedding counts: {'user_id_encoded': 2578, 'book_id_encoded': 4313, 'publisher_encoded': 315, 'country_encoded': 45, 'age_group': 6, 'decade_encoded': 7, 'rating_level': 4}
  Final dataset shape: (197140, 14)
  Label distribution: {0: 0.7427411991478138, 1: 0.2572588008521863}
Splitting data...
Train: 138037 (70.0%)
Validation: 39389 (20.0%)
Test: 19714 (10.0%)
Saving train data to dlrm_book_data/mds_train...


Writing train: 100%|██████████| 138037/138037 [00:10<00:00, 12925.33it/s]


✅ Saved 138037 train samples
Saving validation data to dlrm_book_data/mds_validation...


Writing validation: 100%|██████████| 39389/39389 [00:03<00:00, 13115.30it/s]


✅ Saved 39389 validation samples
Saving test data to dlrm_book_data/mds_test...


Writing test: 100%|██████████| 19714/19714 [00:01<00:00, 13153.28it/s]


✅ Saved 19714 test samples

✅ Data preparation completed!
📊 Dataset ready for DLRM training:
   - Total samples: 197,140
   - Train: 138,037
   - Validation: 39,389
   - Test: 19,714
   - Positive rate: 0.257
   - Dense features: 6
   - Categorical features: 7


## Summary

This notebook has completed the full data exploration and preprocessing pipeline for DLRM-based book recommendation:

### What we accomplished:
1. **Data Loading & Exploration**: Analyzed raw book, user, and rating datasets
2. **Quality Assessment**: Identified missing values and inconsistencies
3. **Data Filtering**: Reduced sparsity by filtering inactive users and unpopular books
4. **Feature Engineering**: Created categorical and dense features optimized for DLRM
5. **Data Preparation**: Split data and saved in MDS format for efficient training
6. **Preprocessing Pipeline**: Complete end-to-end pipeline for DLRM data preparation

### Key Features Created:
- **Categorical Features**: User ID, Book ID, Publisher, Country, Age Group, Publication Decade, Rating Level
- **Dense Features**: Normalized Age, Publication Year, User Activity, Book Popularity, User/Book Average Ratings
- **Target Label**: Binary classification (rating ≥ 6.0)

### Output:
- Training data saved in MDS format at `../dlrm_book_data/`
- Preprocessing artifacts saved in `../book_dlrm_preprocessing.pkl`
- Ready for DLRM model training in next notebook

## 12. Summary and Next Steps

### Key Findings:
1. **High Sparsity**: Original dataset has >99% sparsity
2. **Data Quality Issues**: Missing values in user demographics and book metadata
3. **Filtering Impact**: Aggressive filtering significantly reduces sparsity while maintaining reasonable coverage
4. **Rating Distribution**: Heavy bias towards higher ratings (implicit feedback characteristics)

### Preprocessing Achievements:
- Cleaned and standardized all datasets
- Reduced sparsity through intelligent filtering
- Maintained data consistency across datasets
- Prepared data for machine learning models

### Next Steps:
1. Feature engineering for user and item representations
2. Implementation of Dual-Tower architecture
3. Integration of LLM components for semantic understanding
4. Model training and evaluation framework